In [ ]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

In [ ]:
import warnings
warnings.filterwarnings('ignore')
%config Completer.use_jedi = False # if autocompletion doesnot work in kaggle notebook | hit tab

In [ ]:
# importing the dataset 
df_train = pd.read_csv('../input/emotions-dataset-for-nlp/train.txt', header =None, sep =';', names = ['Input','Sentiment'], encoding='utf-8')
df_test = pd.read_csv('../input/emotions-dataset-for-nlp/test.txt', header = None, sep =';', names = ['Input','Sentiment'],encoding='utf-8')
df_val=pd.read_csv('../input/emotions-dataset-for-nlp/val.txt',header=None,sep=';',names=['Input','Sentiment'],encoding='utf-8')

In [ ]:
df_train.Sentiment.value_counts()

In [ ]:
df_val.Sentiment.value_counts()

In [ ]:
df_test.Sentiment.value_counts()

In [ ]:
df_train.Sentiment.value_counts()

In [ ]:
df_train.head()

In [ ]:
print(df_train.shape, df_test.shape, df_val.shape)

In [ ]:
import matplotlib.pyplot as plt
import seaborn as sns
sns.set()
%config InlineBackend.figure_format = 'retina'

In [ ]:
df_train['Length'] = df_train.Input.apply(lambda x:len(x))

In [ ]:
plt.plot(df_train.Length)
plt.show()

In [ ]:
df_train.Length.max() # max length of our text body 

In [ ]:
# i'm using a text preprocessing library for this 
!pip install text_hammer 
import text_hammer as th

In [ ]:
%%time

from tqdm._tqdm_notebook import tqdm_notebook
tqdm_notebook.pandas()

def text_preprocessing(df,col_name):
    column = col_name
    df[column] = df[column].progress_apply(lambda x:str(x).lower())
    df[column] = df[column].progress_apply(lambda x: th.cont_exp(x)) #you're -> you are; i'm -> i am
    df[column] = df[column].progress_apply(lambda x: th.remove_emails(x))
    df[column] = df[column].progress_apply(lambda x: th.remove_html_tags(x))
#     df[column] = df[column].progress_apply(lambda x: ps.remove_stopwords(x))  
# here we can remove stop-words but in this case removing not, and ,can change the meaning of context 

    df[column] = df[column].progress_apply(lambda x: th.remove_special_chars(x))
    df[column] = df[column].progress_apply(lambda x: th.remove_accented_chars(x))
    df[column] = df[column].progress_apply(lambda x: th.make_base(x)) #ran -> run,
    return(df)

In [ ]:
df_cleaned_train = text_preprocessing(df_train, 'Input')

In [ ]:
df_cleaned_train.head()

In [ ]:
df_cleaned_train['Sentiment']=df_cleaned_train.Sentiment.replace({'joy':0,'anger':1,'love':2,'sadness':3,'fear':4,'surprise':5})
df_test['Sentiment']=df_test.Sentiment.replace({'joy':0,'anger':1,'love':2,'sadness':3,'fear':4,'surprise':5})
df_val['Sentiment']=df_val.Sentiment.replace({'joy':0,'anger':1,'love':2,'sadness':3,'fear':4,'surprise':5})

In [ ]:
from keras.preprocessing.text import Tokenizer

In [ ]:
num_words = 10000 # this means 10000 unique words can be taken 
tokenizer=Tokenizer(num_words,lower=True)
df_total = pd.concat([df_cleaned_train['Input'], df_test.Input], axis = 0)
tokenizer.fit_on_texts(df_total)

In [ ]:
len(tokenizer.word_index) # this is whole unique words in our corpus
# but we are taking only 10000 words in our model

In [ ]:
#from keras.preprocessing.sequence import pad_sequences
from keras.utils import pad_sequences
X_train=tokenizer.texts_to_sequences(df_cleaned_train['Input']) # this converts texts into some numeric sequences 
X_train_pad=pad_sequences(X_train,maxlen=300,padding='post') # this makes the length of all numeric sequences equal 
X_test = tokenizer.texts_to_sequences(df_test.Input)
X_test_pad = pad_sequences(X_test, maxlen = 300, padding = 'post')
X_val = tokenizer.texts_to_sequences(df_val.Input)
X_val_pad = pad_sequences(X_val, maxlen = 300, padding = 'post')

In [ ]:
from keras.utils import to_categorical
y_train = to_categorical(df_cleaned_train.Sentiment.values)
y_test = to_categorical(df_test.Sentiment.values)
y_val = to_categorical(df_val.Sentiment.values)

In [ ]:
print(X_train_pad.shape, X_val_pad.shape)

In [ ]:
import gensim.downloader as api
glove_gensim  = api.load('glove-wiki-gigaword-100') #100 dimension
# more dimension means more deep meaning of words but it may take longer time to download 

In [ ]:
glove_gensim['cat'].shape[0]

In [ ]:
vector_size = 100
gensim_weight_matrix = np.zeros((num_words, vector_size))
gensim_weight_matrix.shape

for word, index in tokenizer.word_index.items():
    if index < num_words:
        if word in glove_gensim:
            gensim_weight_matrix[index] = glove_gensim[word]
        else:
            gensim_weight_matrix[index] = np.zeros(vector_size)


In [ ]:
gensim_weight_matrix.shape

In [ ]:
'''
import os
os.environ["CUDA_VISIBLE_DEVICES"] = ""

from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, LSTM, Embedding, Bidirectional, Dropout
from tensorflow.keras.callbacks import EarlyStopping, ModelCheckpoint

EMBEDDING_DIM = 100

model = Sequential()
model.add(Embedding(input_dim=num_words, output_dim=EMBEDDING_DIM, input_length=X_train_pad.shape[1],
                    weights=[gensim_weight_matrix], trainable=False))
model.add(Dropout(0.2))
model.add(Bidirectional(LSTM(100, return_sequences=True)))
model.add(Dropout(0.2))
model.add(Bidirectional(LSTM(200, return_sequences=True)))
model.add(Dropout(0.2))
model.add(Bidirectional(LSTM(100, return_sequences=False)))
model.add(Dense(6, activation='softmax'))

model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])

es = EarlyStopping(monitor='val_loss', mode='min', verbose=1, patience=5)
mc = ModelCheckpoint('./model.h5', monitor='val_accuracy', mode='max', verbose=1, save_best_only=True)

history_embedding = model.fit(X_train_pad, y_train, epochs=25, batch_size=120, validation_data=(X_val_pad, y_val),
                              verbose=1, callbacks=[es, mc])
'''

In [ ]:
'''
plt.plot(history_embedding.history['accuracy'],c='b',label='train accuracy')
plt.plot(history_embedding.history['val_accuracy'],c='r',label='validation accuracy')
plt.legend(loc='lower right')
plt.show()
'''

In [ ]:
#model.evaluate(X_test_pad, y_test) 

In [ ]:
#y_pred =   np.argmax(model.predict(X_test_pad), axis  =  1)

In [ ]:
#y_true = np.argmax(y_test, axis = 1)

In [ ]:
#from sklearn import metrics
#print(metrics.classification_report(y_pred, y_true))

In [ ]:
'''
def get_key(value):
    dictionary={'joy':0,'anger':1,'love':2,'sadness':3,'fear':4,'surprise':5}
    for key,val in dictionary.items():
          if (val==value):
            return key
'''

In [ ]:
'''
def predict(sentence):
    sentence_lst=[]
    sentence_lst.append(sentence)
    sentence_seq=tokenizer.texts_to_sequences(sentence_lst)
    sentence_padded=pad_sequences(sentence_seq,maxlen=300,padding='post')
    ans=get_key(model.predict_classes(sentence_padded))
    print("The emotion predicted is",ans)
    
'''

extra kaam

In [ ]:
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, LSTM, Embedding, Bidirectional, Dropout
from tensorflow.keras.callbacks import EarlyStopping, ModelCheckpoint

EMBEDDING_DIM = 100

model = Sequential()
model.add(Embedding(input_dim=num_words, output_dim=EMBEDDING_DIM, input_length=X_train_pad.shape[1],
                    weights=[gensim_weight_matrix], trainable=False))
model.add(Dropout(0.2))
model.add(Bidirectional(LSTM(100, return_sequences=True)))
model.add(Dropout(0.2))
model.add(Bidirectional(LSTM(200, return_sequences=True)))
model.add(Dropout(0.2))
model.add(Bidirectional(LSTM(100, return_sequences=False)))
model.add(Dense(6, activation='softmax'))

model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])

es = EarlyStopping(monitor='val_loss', mode='min', verbose=1, patience=5)
mc = ModelCheckpoint('./best_model_weights.h5', monitor='val_accuracy', mode='max', verbose=1,
                     save_best_only=True)

history_embedding = model.fit(X_train_pad, y_train, epochs=35, batch_size=120, validation_data=(X_val_pad, y_val),
                              verbose=1, callbacks=[es, mc])



In [ ]:
plt.plot(history_embedding.history['accuracy'],c='b',label='train accuracy')
plt.plot(history_embedding.history['val_accuracy'],c='r',label='validation accuracy')
plt.legend(loc='lower right')
plt.show()

In [ ]:
model.evaluate(X_test_pad, y_test) 

In [ ]:
y_pred =   np.argmax(model.predict(X_test_pad), axis  =  1)

In [ ]:
y_true = np.argmax(y_test, axis = 1)

In [ ]:
from sklearn import metrics
print(metrics.classification_report(y_pred, y_true))

In [ ]:
def get_key(value):
    dictionary={'joy':0,'anger':1,'love':2,'sadness':3,'fear':4,'surprise':5}
    for key,val in dictionary.items():
          if (val==value):
            return key

In [ ]:
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, LSTM, Embedding, Bidirectional, Dropout
from tensorflow.keras.preprocessing.sequence import pad_sequences
import numpy as np

# Assuming you have your test data X_test_pad

EMBEDDING_DIM = 100
num_words = 10000  # Example value, adjust according to your data

# Define the model architecture
model = Sequential()
model.add(Embedding(input_dim=num_words, output_dim=EMBEDDING_DIM, input_length=X_test_pad.shape[1]))
model.add(Dropout(0.2))
model.add(Bidirectional(LSTM(100, return_sequences=True)))
model.add(Dropout(0.2))
model.add(Bidirectional(LSTM(200, return_sequences=True)))
model.add(Dropout(0.2))
model.add(Bidirectional(LSTM(100, return_sequences=False)))
model.add(Dense(6, activation='softmax'))

# Load the saved model weights
model.load_weights('./best_model_weights.h5')

# Compile the model (if needed)
model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])

# Predict sentiment on the test dataset
predictions = model.predict(X_test_pad)

# Get the predicted sentiment label for each prediction
sentiment_labels = np.argmax(predictions, axis=1)

label_to_sentiment = {
    0: "joy",
    1: "anger",
    2: "love",
    3: "sadness",
    4: "fear",
    5: "surprise"
}
# Convert sentiment labels to actual sentiments (assuming you have a label-to-sentiment mapping)
sentiments = [label_to_sentiment[label] for label in sentiment_labels]

# Print the predicted sentiments
#print(sentiments)


In [ ]:
import pandas as pd

# Assuming you have a DataFrame called 'test_df' with the test data and labels

# Create a new column 'Predicted Label' in the DataFrame
df_test['Predicted Label'] = sentiment_labels

# Compare the predicted labels with the true labels
df_test['Prediction Correct'] = df_test['Predicted Label'] == df_test['Sentiment']

# Print the DataFrame to see the results
print(df_test)


In [ ]:
from sklearn.metrics import accuracy_score

# Calculate the accuracy
accuracy = accuracy_score(df_test['Sentiment'], df_test['Predicted Label'])

# Print the accuracy
print("Accuracy: {:.2f}%".format(accuracy * 100))


In [ ]:
len(sentiments)

In [ ]:
#now trying to get sentiments/emotions on our unlabelled pheme dataset

df_pheme = pd.read_csv('/kaggle/input/pheme-dataset-for-rumour-detection/dataset.csv')

In [ ]:
df_pheme

In [ ]:

# Create New DataFrame of Specific column by DataFrame.assign() method.
df4 = pd.DataFrame().assign(Input=df_pheme['text'], label=df_pheme['is_rumor'])
print(df4)


In [ ]:
df4['Length'] = df4.Input.apply(lambda x:len(x))

In [ ]:
plt.plot(df4.Length)
plt.show()

In [ ]:
df4.Length.max() # max length of our text body 

In [ ]:
df_cleaned_train_4 = text_preprocessing(df4, 'Input')

In [ ]:
df4

In [ ]:
df_total_4 = pd.concat([df_cleaned_train_4['Input'], df4.Input], axis = 0)
tokenizer.fit_on_texts(df_total_4)

In [ ]:
df_total_4

In [ ]:
X_train_4=tokenizer.texts_to_sequences(df_cleaned_train_4['Input']) # this converts texts into some numeric sequences 
X_train_pad_4=pad_sequences(X_train_4,maxlen=300,padding='post')

In [ ]:
print(X_train_pad_4.shape)

In [ ]:
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, LSTM, Embedding, Bidirectional, Dropout
from tensorflow.keras.preprocessing.sequence import pad_sequences
import numpy as np

# Assuming you have your test data X_test_pad

EMBEDDING_DIM = 100
num_words = 10000  # Example value, adjust according to your data

# Define the model architecture
model = Sequential()
model.add(Embedding(input_dim=num_words, output_dim=EMBEDDING_DIM, input_length=X_test_pad.shape[1]))
model.add(Dropout(0.2))
model.add(Bidirectional(LSTM(100, return_sequences=True)))
model.add(Dropout(0.2))
model.add(Bidirectional(LSTM(200, return_sequences=True)))
model.add(Dropout(0.2))
model.add(Bidirectional(LSTM(100, return_sequences=False)))
model.add(Dense(6, activation='softmax'))

# Load the saved model weights
model.load_weights('./best_model_weights.h5')

# Compile the model (if needed)
model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])

# Predict sentiment on the test dataset
predictions = model.predict(X_train_pad_4)

# Get the predicted sentiment label for each prediction
sentiment_labels = np.argmax(predictions, axis=1)

label_to_sentiment = {
    0: "joy",
    1: "anger",
    2: "love",
    3: "sadness",
    4: "fear",
    5: "surprise"
}
# Convert sentiment labels to actual sentiments (assuming you have a label-to-sentiment mapping)
sentiments = [label_to_sentiment[label] for label in sentiment_labels]

# Print the predicted sentiments
#print(sentiments)


In [ ]:
df4['Predicted_Label'] = sentiments

In [ ]:
df4

In [ ]:
df4.Predicted_Label.value_counts()

In [ ]:
df4.to_csv('emotion.csv')